In [0]:
#importing the data
sales_transactions_raw = spark.read.option("header", True) \
    .csv("/Volumes/main/default/data_files_scenario-3/sales_transactions_jan_2025.csv")
product_master_raw = spark.read.option("header", True) \
    .csv("/Volumes/main/default/data_files_scenario-3/product_master.csv")
store_master_raw = spark.read.option("header", True) \
    .csv("/Volumes/main/default/data_files_scenario-3/store_master.csv")


In [0]:
display(sales_transactions_raw.head())
display(product_master_raw.head())
display(store_master_raw.head())

Row(transaction_id='6e8944c8-2358-4066-b47a-f9fb5cfaaca8', transaction_timestamp='2025-01-01 06:32:00', store_id='STR007', product_id='PRD104', quantity='2', unit_price='979.15', discount='0', total_amount='1958.3', currency='EUR')

Row(product_id='PRD101', product_name='iPhone 14', category='Electronics', brand='Apple', standard_price='999.0')

Row(store_id='STR001', store_name='Hyderabad Central', region='South', country='India')

In [0]:
#takes the raw csv data and creates delta table
#Bronze layer
sales_transactions_raw.write.format("delta").mode("overwrite") \
    .saveAsTable("main.default.bronze_sales_s3")

product_master_raw.write.format("delta").mode("overwrite") \
    .saveAsTable("main.default.bronze_product_s3")

store_master_raw.write.format("delta").mode("overwrite") \
    .saveAsTable("main.default.bronze_store_s3")

In [0]:
#Read the bronze tables
from pyspark.sql import functions as F
from pyspark.sql.window import Window

bronze_sales = spark.table("main.default.bronze_sales_s3")
bronze_products = spark.table("main.default.bronze_product_s3")
bronze_stores = spark.table("main.default.bronze_store_s3")


In [0]:
#Adding the watermark logic so we dont have to reprocess the data every time a new transaction adds
from pyspark.sql import functions as F

last_processed_ts = None

if spark.catalog.tableExists("main.default.silver_sales_s3"):
    last_processed_ts = spark.sql("""
        SELECT max(transaction_timestamp)
        FROM main.default.silver_sales_s3
    """).collect()[0][0]
if last_processed_ts:
    bronze_sales = bronze_sales.filter(
        F.to_timestamp("transaction_timestamp") > F.lit(last_processed_ts)
    )


In [0]:
from pyspark.sql import functions as F

silver_casted = (
    bronze_sales
    .withColumn("quantity", F.col("quantity").cast("int"))
    .withColumn("unit_price", F.col("unit_price").cast("double"))
    .withColumn("discount", F.col("discount").cast("double"))
    .withColumn("total_amount", F.col("total_amount").cast("double"))
    .withColumn(
        "transaction_timestamp",
        F.to_timestamp("transaction_timestamp")
    )
)


In [0]:
#Handlng the null values
silver_casted = (
    silver_casted.filter(
        F.col("transaction_id").isNotNull() &
        F.col("transaction_timestamp").isNotNull() &
        F.col("store_id").isNotNull() &
        F.col("product_id").isNotNull()
    )
)

In [0]:
#SILVER LAYER
#finding the total_amount
silver_prepared = (
    silver_casted
    .withColumn(
        "transaction_timestamp",
        F.to_utc_timestamp("transaction_timestamp", "UTC")
    )
    .withColumn(
        "total_amount",
        F.round(
            F.col("quantity") * F.col("unit_price") - F.col("discount"), 2
        )
    )
)


In [0]:
#DQ quarantine code
dq_invalid = silver_prepared.filter(
    (F.col("quantity") <= 0) |
    (F.col("unit_price") <= 0) |
    (F.col("total_amount") < 0)
)


In [0]:
#removing invalid data
dq_valid = silver_prepared.filter(
    (F.col("quantity") > 0) &
    (F.col("unit_price") > 0) &
    (F.col("total_amount") >= 0)
)

invalid_store = (
    dq_valid
    .join(
        bronze_stores.select("store_id"),
        on="store_id",
        how="left_anti"
    )
)



In [0]:
#removes invalid store_id (in the data we have STR999 which is an invalid store, so we remove it)
silver_valid = (
    dq_valid
    .join(
        bronze_products.select("product_id"),
        on="product_id",
        how="inner"
    )
    .join(
        bronze_stores.select("store_id", "region", "country"),
        on="store_id",
        how="inner"
    )
)

In [0]:
display(silver_valid)

store_id product_id transaction_id transaction_timestamp quantity unit_price discount total_amount currency region country STR007 PRD104 6e8944c8-2358-4066-b47a-f9fb5cfaaca8 2025-01-01T06:32:00.000Z 2 979.15 0.0 1958.3 EUR Europe Germany STR006 PRD102 5a54ddad-1d0a-441b-8cc9-7e309c409dc6 2025-01-01T04:53:00.000Z 5 533.05 0.0 2665.25 EUR Europe UK STR005 PRD107 c930ad8a-b0e4-4f8c-9142-c985aea6f06b 2025-01-01T12:47:00.000Z 4 1189.88 0.0 4759.52 INR West USA STR001 PRD105 64110360-7a32-461d-b0cd-34a010873ff1 2025-01-01T20:31:00.000Z 2 1176.87 20.0 2333.74 EUR South India STR006 PRD109 c58bbeb5-5b7a-4ee8-85ba-0e8a27322a8c 2025-01-01T14:41:00.000Z 3 133.43 20.0 380.29 INR Europe UK STR001 PRD105 b05f7cf2-d5d7-409e-9db7-63f9dfd16895 2025-01-01T16:49:00.000Z 3 838.26 0.0 2514.78 INR South India STR008 PRD103 980273d3-85ff-4af0-b450-68e00a86740d 2025-01-01T10:09:00.000Z 5 1425.77 50.0 7078.85 EUR APAC Singapore STR008 PRD101 ed6d7c72-ec1a-437f-9adf-5d000b2f2c9e 2025-01-01T12:02:00.000Z 2 573.7 10.0 1137.4 USD APAC Singapore STR003 PRD106 1006b00d-8252-4ba6-9309-60de4a2809c8 2025-01-01T03:51:00.000Z 2 332.5 10.0 655.0 USD West India STR006 PRD108 92eb1964-df8f-4f43-a5a1-6a56f39f4e42 2025-01-01T05:44:00.000Z 5 941.54 50.0 4657.7 EUR Europe UK STR003 PRD101 a3f6fa5d-4b84-4f48-8d1f-5d293c037da7 2025-01-01T13:11:00.000Z 3 994.7 0.0 2984.1 USD West India STR002 PRD104 1fb61961-58e8-4f91-a14c-ca23bab0d689 2025-01-01T16:41:00.000Z 2 54.01 50.0 58.02 INR South India STR003 PRD103 c33d2586-eafd-44bd-b289-bf86c317a541 2025-01-01T21:55:00.000Z 5 826.72 0.0 4133.6 USD West India STR001 PRD109 abd0e807-a03b-49ab-91c8-e55f0fa915be 2025-01-01T02:52:00.000Z 2 1264.17 20.0 2508.34 INR South India STR007 PRD109 7cb3c309-5c74-406f-9f1e-995a1b59a5f8 2025-01-01T18:29:00.000Z 5 845.41 0.0 4227.05 INR Europe Germany STR009 PRD103 60370a17-7be1-4813-bb45-54b5073d1b15 2025-01-01T12:39:00.000Z 2 1118.32 10.0 2226.64 EUR APAC Australia STR005 PRD106 fb0991af-23fa-4edc-9103-00f0b3b13ddb 2025-01-01T12:18:00.000Z 2 777.28 0.0 1554.56 EUR West USA STR009 PRD103 bc7fe454-90d9-4330-a1dc-c29a89acc89d 2025-01-01T20:11:00.000Z 1 1104.87 0.0 1104.87 USD APAC Australia STR006 PRD109 de597c06-c933-4042-bb49-3ab5a316c877 2025-01-01T15:56:00.000Z 3 108.23 10.0 314.69 INR Europe UK STR001 PRD109 01da61f9-6511-4dd3-a551-51f4c7320ae7 2025-01-01T12:51:00.000Z 4 389.26 0.0 1557.04 USD South India STR004 PRD102 97233a6b-b0d2-458d-9731-b7db8aa30779 2025-01-01T13:08:00.000Z 3 1320.25 10.0 3950.75 EUR East USA STR006 PRD103 3664e7c3-a0ad-4066-888a-54a6c716879f 2025-01-01T11:40:00.000Z 3 842.97 50.0 2478.91 USD Europe UK STR008 PRD107 81370e27-32e3-47e9-a8e7-d58af55284ce 2025-01-01T12:21:00.000Z 4 504.66 10.0 2008.64 USD APAC Singapore STR002 PRD103 adee5a54-1bde-4925-9017-de186d8c850f 2025-01-01T12:19:00.000Z 5 1310.52 10.0 6542.6 USD South India STR002 PRD101 660fbd1f-a403-45ea-a9fe-7861f588a34f 2025-01-01T17:03:00.000Z 3 460.16 20.0 1360.48 EUR South India STR010 PRD110 1a33f95a-4d52-4fe5-a60b-7298295dd110 2025-01-01T05:40:00.000Z 4 832.07 0.0 3328.28 USD APAC Japan STR005 PRD109 4ec7c7d8-1d71-4dd5-b4c4-3bb26a9a8703 2025-01-01T23:55:00.000Z 2 922.06 50.0 1794.12 USD West USA STR008 PRD101 3e4ff513-f311-4024-966a-a03990064ba9 2025-01-01T17:15:00.000Z 4 767.92 20.0 3051.68 EUR APAC Singapore STR010 PRD101 913e89d4-ae3a-4991-b7c7-3cdd9c131f85 2025-01-01T18:33:00.000Z 5 399.85 0.0 1999.25 INR APAC Japan STR008 PRD110 5199619e-d6d2-44b0-8f8f-19e2ac455146 2025-01-01T08:01:00.000Z 3 1379.87 0.0 4139.61 INR APAC Singapore STR007 PRD107 4daa3bc5-dc1b-4391-96b1-c69afcbad184 2025-01-01T20:59:00.000Z 2 1104.08 10.0 2198.16 EUR Europe Germany STR003 PRD101 6646a1c2-c2fd-4cc3-918b-00a34d964acf 2025-01-01T21:33:00.000Z 4 834.0 0.0 3336.0 EUR West India STR005 PRD109 09bfbe0a-bf9c-45de-becb-8c1c36956c8c 2025-01-01T02:00:00.000Z 3 1426.54 10.0 4269.62 EUR West USA STR007 PRD102 4f13a306-7b13-475d-bf40-6633bbad3696 2025-01-01T11:47:00.000Z 1 215.63 50.0 165.63 USD Europe Germany STR002 PRD109 70947cb

In [0]:
#removing duplicates of each repeated transaction and use only its recent transaction data
window_spec = (
    Window
    .partitionBy("transaction_id")
    .orderBy(F.col("transaction_timestamp").desc())
)

silver_deduped = (
    silver_valid
    .withColumn("row_num", F.row_number().over(window_spec))
    .filter(F.col("row_num") == 1)
    .drop("row_num")
)

In [0]:
silver_deduped.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("main.default.silver_sales_s3")


In [0]:
#writing quarantine tables
dq_invalid.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("main.default.silver_sales_dq_quarantine_s3")

invalid_store.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("main.default.silver_sales_invalid_store_s3")

In [0]:
display(spark.table("main.default.silver_sales_dq_quarantine_s3"))

transaction_id transaction_timestamp store_id product_id quantity unit_price discount total_amount currency 88e76830-9a92-4228-8db7-b76e05817f60 2025-01-01T11:53:00.000Z STR999 PRD109 -1 1453.23 10.0 -1463.23 INR 79408888-ce1c-4d4d-aaee-179c69614c18 2025-01-01T20:18:00.000Z STR999 PRD101 -1 1380.77 20.0 -1400.77 USD 7e556afc-cd98-4f43-a0e6-de0b20979521 2025-01-01T07:48:00.000Z STR010 PRD105 -2 1468.15 10.0 -2946.3 EUR 8be760bf-e7bd-486a-83fe-7f31443d15d0 2025-01-01T22:38:00.000Z STR003 PRD105 -3 383.66 20.0 -1170.98 INR 065ec6a1-a5bc-4c34-b08a-1af04134f633 2025-01-01T09:50:00.000Z STR008 PRD107 -1 805.73 20.0 -825.73 USD da726b3c-ce6f-439f-a014-f302a574db2d 2025-01-01T04:54:00.000Z STR003 PRD110 -4 987.03 50.0 -3998.12 INR 383f8ae3-fee3-4c42-8757-88c7e90fced5 2025-01-01T03:38:00.000Z STR006 PRD101 -5 930.45 10.0 -4662.25 USD f687df60-7113-49df-a8a9-89b9675e94ea 2025-01-01T09:22:00.000Z STR002 PRD107 -5 1100.16 50.0 -5550.8 EUR e1494b5d-d340-4e76-8b20-c64c30f7077c 2025-01-01T02:54:00.000Z STR004 PRD109 -1 76.95 10.0 -86.95 USD 556778eb-1caa-4676-8c08-08f662d6343e 2025-01-01T03:55:00.000Z STR002 PRD101 -5 167.0 0.0 -835.0 EUR ee564dae-ee32-4928-95d7-030949278d30 2025-01-01T11:55:00.000Z STR008 PRD107 -2 713.78 0.0 -1427.56 USD 3b093a35-ec8d-4f18-8bec-9b6acbcaa55b 2025-01-01T07:09:00.000Z STR002 PRD105 -5 662.04 20.0 -3330.2 EUR 90a8d8e5-4890-466c-bd0e-771fdf84a61a 2025-01-01T16:07:00.000Z STR010 PRD110 -3 574.53 0.0 -1723.59 INR a3b97401-ecb3-4fb0-9e1c-c9f4070f6a23 2025-01-01T10:04:00.000Z STR003 PRD104 -2 1479.28 0.0 -2958.56 USD e479a94e-481b-4165-83d3-731e2a1c37fe 2025-01-01T14:26:00.000Z STR007 PRD103 -1 1388.27 0.0 -1388.27 EUR e4df33bb-8437-4f71-ae0b-7d813b7e12fe 2025-01-01T10:52:00.000Z STR003 PRD106 -1 1234.41 0.0 -1234.41 INR 4f04e2a8-5fbe-41e0-aac5-99bba1e459db 2025-01-01T23:20:00.000Z STR010 PRD110 -1 113.8 10.0 -123.8 USD 5edea49b-b370-4a3f-96d2-d8091ffe699a 2025-01-01T12:26:00.000Z STR003 PRD106 -5 1261.73 20.0 -6328.65 USD ff7fc772-9ad7-4799-a9a2-112984bef9aa 2025-01-01T23:33:00.000Z STR007 PRD109 -2 1176.04 0.0 -2352.08 EUR e27f62f1-5f78-4673-8ec8-7a241a1e7d58 2025-01-01T02:24:00.000Z STR001 PRD108 -2 553.19 0.0 -1106.38 INR ab2c50d1-61e5-47c0-9b0a-0b2ab859716a 2025-01-01T14:34:00.000Z STR006 PRD108 -1 1365.23 0.0 -1365.23 EUR b49e62de-7ded-41c5-89fc-68e43dcc51c0 2025-01-01T07:00:00.000Z STR002 PRD108 -1 147.65 0.0 -147.65 EUR 919c003e-25c0-44f8-a8a4-572d7a704fc0 2025-01-02T13:59:00.000Z STR009 PRD103 -3 776.82 0.0 -2330.46 INR 317f7079-56ab-49ad-9170-b7339ce5389a 2025-01-02T22:01:00.000Z STR008 PRD106 -1 1154.94 50.0 -1204.94 USD 8843d178-4f83-4ac7-b218-93f8ee74964e 2025-01-02T09:10:00.000Z STR005 PRD105 -2 671.25 0.0 -1342.5 EUR bc839c20-bbb2-4b4a-aebf-43ab2cda1add 2025-01-02T02:40:00.000Z STR010 PRD109 -5 1017.46 0.0 -5087.3 USD 11f8328e-7ba5-476b-9189-c4bbcb43f61d 2025-01-02T19:45:00.000Z STR008 PRD103 -1 407.93 0.0 -407.93 EUR fddc684b-4a2b-47e9-98e5-3d06b49f43f3 2025-01-02T01:20:00.000Z STR008 PRD109 -2 545.47 10.0 -1100.94 USD 0821d49a-417b-460a-87ef-3de55f064948 2025-01-02T23:28:00.000Z STR009 PRD108 -3 579.89 10.0 -1749.67 EUR 2033e7bd-290a-47f2-8b23-134fc9a90ece 2025-01-02T05:00:00.000Z STR009 PRD103 -4 1227.12 0.0 -4908.48 USD 36072d6c-5d6e-4b42-887e-4baaa96b9676 2025-01-02T13:07:00.000Z STR007 PRD109 -1 452.85 0.0 -452.85 INR c0779b4d-3b8f-4e96-8974-fa9b98626fde 2025-01-02T00:36:00.000Z STR006 PRD104 -3 352.54 20.0 -1077.62 EUR bc858b5a-f040-4878-8554-2b130b65c0fe 2025-01-02T19:13:00.000Z STR003 PRD110 -2 673.78 0.0 -1347.56 INR 34cb033e-2e23-4f8f-a769-53267e1adea1 2025-01-02T17:51:00.000Z STR006 PRD105 -3 1006.17 0.0 -3018.51 USD dce553b3-8208-4b02-b407-0f22b2c23bb9 2025-01-02T23:30:00.000Z STR003 PRD103 -2 535.39 0.0 -1070.78 INR 1276d7d0-4918-49e4-b209-69054ad59f1a 2025-01-02T00:46:00.000Z STR009 PRD110 -3 1426.45 0.0 -4279.35 USD cc5e796b-a9ed-44d2-aed7-20ea140dc1bf 2025-01-02T18:19:00.000Z STR004 PRD105 -3 1399.21 0.0 -4197.63 EUR a71750a3-0d12-4b45-9932-dd48b4813a7e 2025-01-02T21:25:00.000Z STR00

In [0]:
#Gold layer
#analysis about daily sales
silver_sales = spark.table("main.default.silver_sales_s3")

gold_daily_sales = (
    silver_sales
    .withColumn("sales_date", F.to_date("transaction_timestamp"))
    .groupBy("sales_date", "region", "country")
    .agg(
        F.sum("total_amount").alias("total_revenue"),
        F.countDistinct("transaction_id").alias("transactions"),
        F.sum("quantity").alias("units_sold")
    )
    .withColumn(
        "avg_order_value",
        F.round(F.col("total_revenue") / F.col("transactions"), 2)
    )
)

gold_daily_sales.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("main.default.gold_daily_sales_s3")


In [0]:
display(silver_sales)

store_id product_id transaction_id transaction_timestamp quantity unit_price discount total_amount currency region country STR002 PRD104 0009c93e-ce32-486b-8640-c36e31749af8 2025-01-22T21:32:00.000Z 2 1275.03 50.0 2500.06 INR South India STR002 PRD104 000abdb8-45af-4cff-8f60-2cca9dafe67d 2025-01-20T11:36:00.000Z 5 1366.49 20.0 6812.45 INR South India STR010 PRD107 000ee135-f3df-43f2-ab5c-125dd611f344 2025-01-21T02:56:00.000Z 3 1086.96 10.0 3250.88 USD APAC Japan STR010 PRD105 000f460e-3689-4773-92ad-78d5299e4126 2025-01-30T06:28:00.000Z 5 1118.42 50.0 5542.1 EUR APAC Japan STR009 PRD106 0015c76c-a3f2-47c1-ad4f-1c3273b660ef 2025-01-04T09:32:00.000Z 3 504.81 10.0 1504.43 USD APAC Australia STR001 PRD108 00169841-3d76-4a4d-89e0-8476f2bc0545 2025-01-09T12:10:00.000Z 5 98.77 10.0 483.85 INR South India STR008 PRD105 00195996-a825-4444-9640-db8a0d3aff55 2025-01-27T20:15:00.000Z 4 676.38 20.0 2685.52 INR APAC Singapore STR007 PRD108 001e31f1-c07e-420d-8e71-5196a357565a 2025-01-13T18:30:00.000Z 3 785.23 0.0 2355.69 INR Europe Germany STR001 PRD101 002266b5-3bea-4c60-bc6e-f019d108ca42 2025-01-17T14:53:00.000Z 2 477.95 0.0 955.9 EUR South India STR007 PRD110 0029d0a1-fe2b-41ce-96d4-33b86e8fd64d 2025-01-06T01:41:00.000Z 2 264.82 0.0 529.64 EUR Europe Germany STR010 PRD108 002ad2a1-f43f-4076-b6fd-96f58e50b805 2025-01-17T16:48:00.000Z 1 533.17 0.0 533.17 EUR APAC Japan STR001 PRD105 002b75dd-b90a-4de9-a1d8-503fd237d971 2025-01-09T14:19:00.000Z 3 1191.04 20.0 3553.12 INR South India STR009 PRD102 0031f3de-b15d-4ae4-abcf-b2ad48197f75 2025-01-01T23:42:00.000Z 5 1360.38 20.0 6781.9 INR APAC Australia STR002 PRD108 003b8716-793b-45fd-a849-81230cd2724a 2025-01-22T11:01:00.000Z 2 1243.67 0.0 2487.34 EUR South India STR010 PRD102 003d684a-ca00-4730-ac84-675d24cea615 2025-01-06T22:34:00.000Z 1 584.05 0.0 584.05 INR APAC Japan STR001 PRD102 0044ca39-a3d3-445b-9e43-14c6833585bf 2025-01-21T15:59:00.000Z 1 919.84 10.0 909.84 INR South India STR007 PRD105 00466a0b-83e9-47aa-9844-753c62062b2e 2025-01-20T04:04:00.000Z 1 121.16 0.0 121.16 USD Europe Germany STR006 PRD108 00480480-e8f6-4b60-9481-c7c5be06d5ae 2025-01-08T11:51:00.000Z 3 1133.01 10.0 3389.03 INR Europe UK STR001 PRD103 00498b2c-1485-4f85-a5ab-47b4a4de543f 2025-01-03T00:43:00.000Z 1 133.63 0.0 133.63 EUR South India STR006 PRD103 004d6231-ff15-4ceb-a226-70180868a4ef 2025-01-10T23:10:00.000Z 3 1423.8 20.0 4251.4 EUR Europe UK STR007 PRD108 004dc0bc-6996-4685-a1a0-3354fa3d8590 2025-01-16T03:16:00.000Z 4 396.01 0.0 1584.04 EUR Europe Germany STR009 PRD110 0052c14d-0bcb-4288-a64f-708b9ac8d545 2025-01-13T13:45:00.000Z 1 945.77 50.0 895.77 INR APAC Australia STR002 PRD102 0055812c-95b0-4be3-9183-6e6540160463 2025-01-11T22:47:00.000Z 3 640.94 20.0 1902.82 INR South India STR008 PRD101 005cee86-bc62-4bad-a209-fed9e6c10b5f 2025-01-04T10:55:00.000Z 2 984.9 10.0 1959.8 USD APAC Singapore STR003 PRD110 0065939a-47bc-44cd-b63f-4c7531064cd3 2025-01-29T04:35:00.000Z 4 1006.66 20.0 4006.64 INR West India STR007 PRD110 00668a02-8cf8-4a77-a57c-7955f0e070e1 2025-01-29T15:05:00.000Z 5 1215.74 10.0 6068.7 INR Europe Germany STR003 PRD108 006703f3-0366-48c9-b07d-aed5ba059646 2025-01-04T00:39:00.000Z 4 1061.64 50.0 4196.56 USD West India STR009 PRD101 00674236-3d3a-4e7a-b365-bcec994f9cbb 2025-01-22T19:38:00.000Z 4 510.85 0.0 2043.4 INR APAC Australia STR001 PRD103 0068135e-1257-468a-adb4-98d329589143 2025-01-05T00:40:00.000Z 2 1441.02 0.0 2882.04 EUR South India STR001 PRD110 006a3926-afce-4e5a-96ba-367bbb0f2608 2025-01-21T11:24:00.000Z 2 1153.01 0.0 2306.02 EUR South India STR009 PRD106 006e4e71-e97a-438f-9ebc-5ceb9df66185 2025-01-07T03:08:00.000Z 2 784.57 20.0 1549.14 INR APAC Australia STR002 PRD103 0073bdcb-7892-47b8-b02d-2715eacb4371 2025-01-27T04:54:00.000Z 2 1108.04 10.0 2206.08 USD South India STR005 PRD106 0073c0bc-06ac-421d-9387-5849c0464f1b 2025-01-11T18:48:00.000Z 4 464.27 0.0 1857.08 USD West USA STR007 PRD106 0076486b-f39d-4b1f-92be-aaf02c0067b7 2025-01-08T22:08:00.000Z 2 506.38 0.0 1012.76 INR Europe G

In [0]:
display(gold_daily_sales)

sales_date region country total_revenue transactions units_sold avg_order_value 2025-01-22 South India 363837.64999999973 152 463 2393.67 2025-01-20 South India 356941.44000000006 152 457 2348.3 2025-01-21 APAC Japan 188628.41999999993 78 247 2418.31 2025-01-30 APAC Japan 139447.30000000002 64 191 2178.86 2025-01-04 APAC Australia 162506.4100000001 70 211 2321.52 2025-01-09 South India 365979.67999999993 152 466 2407.76 2025-01-27 APAC Singapore 144371.12000000002 67 204 2154.79 2025-01-13 Europe Germany 172302.83999999997 67 212 2571.68 2025-01-17 South India 380191.83999999985 152 470 2501.26 2025-01-06 Europe Germany 161827.1 71 209 2279.25 2025-01-17 APAC Japan 170782.25999999998 74 212 2307.87 2025-01-01 APAC Australia 180544.12999999992 72 228 2507.56 2025-01-06 APAC Japan 115140.91000000003 68 185 1693.25 2025-01-21 South India 326980.6600000001 134 385 2440.15 2025-01-20 Europe Germany 159909.69000000003 69 211 2317.53 2025-01-08 Europe UK 196748.24999999997 77 234 2555.17 2025-01-03 South India 377884.71 152 459 2486.08 2025-01-10 Europe UK 153962.58000000002 65 199 2368.66 2025-01-16 Europe Germany 133975.86000000004 58 177 2309.93 2025-01-13 APAC Australia 140708.91 58 193 2426.02 2025-01-11 South India 372146.03000000014 147 454 2531.61 2025-01-04 APAC Singapore 167424.75 69 226 2426.45 2025-01-29 West India 149171.93999999997 62 208 2406.0 2025-01-29 Europe Germany 179147.61000000007 74 225 2420.91 2025-01-04 West India 155504.55 73 226 2130.2 2025-01-22 APAC Australia 163898.28000000003 72 215 2276.37 2025-01-05 South India 322617.99 144 446 2240.4 2025-01-07 APAC Australia 124026.19999999998 54 176 2296.78 2025-01-27 South India 312673.17 136 422 2299.07 2025-01-11 West USA 157035.54 68 201 2309.35 2025-01-08 Europe Germany 151829.04999999996 67 214 2266.11 2025-01-04 Europe Germany 135078.50000000003 69 201 1957.66 2025-01-09 East USA 161823.54999999996 77 228 2101.6 2025-01-18 South India 297390.86000000004 136 393 2186.7 2025-01-23 Europe Germany 146493.16 61 184 2401.53 2025-01-30 South India 314417.1999999999 135 434 2329.02 2025-01-20 Europe UK 151467.71 67 193 2260.71 2025-01-07 Europe UK 201792.47999999992 76 232 2655.16 2025-01-20 APAC Australia 155250.62999999998 61 195 2545.09 2025-01-10 East USA 163478.9 67 216 2439.98 2025-01-20 East USA 222570.26999999993 88 279 2529.21 2025-01-17 Europe UK 162982.62999999995 70 209 2328.32 2025-01-13 APAC Japan 147522.71000000002 59 191 2500.38 2025-01-24 APAC Singapore 207115.63999999996 86 252 2408.32 2025-01-02 West USA 182208.72999999995 80 240 2277.61 2025-01-12 West USA 137936.53999999998 64 175 2155.26 2025-01-21 West USA 199523.90000000008 90 281 2216.93 2025-01-07 West USA 151031.96000000005 63 183 2397.33 2025-01-22 Europe UK 180346.34000000005 72 216 2504.81 2025-01-19 West India 212667.81999999998 86 264 2472.88 2025-01-08 South India 285238.78 138 396 2066.95 2025-01-14 West USA 151174.52000000005 68 202 2223.15 2025-01-01 APAC Singapore 163379.87999999998 70 211 2334.0 2025-01-16 West USA 190681.11999999997 80 242 2383.51 2025-01-18 West India 174157.38999999998 74 236 2353.48 2025-01-21 Europe Germany 189019.48999999993 84 256 2250.23 2025-01-28 West India 171706.63999999996 72 203 2384.81 2025-01-15 APAC Australia 139036.27000000002 60 177 2317.27 2025-01-04 South India 329118.74 140 431 2350.85 2025-01-07 South India 274888.6599999999 127 355 2164.48 2025-01-21 East USA 182842.75000000006 77 242 2374.58 2025-01-18 APAC Australia 159696.56 66 202 2419.64 2025-01-23 East USA 170755.00000000003 72 222 2371.6 2025-01-05 East USA 197505.52999999997 74 234 2668.99 2025-01-03 APAC Singapore 215964.39 83 277 2601.98 2025-01-11 APAC Australia 136400.46000000002 67 180 2035.83 2025-01-21 Europe UK 137746.10999999993 65 192 2119.17 2025-01-02 East USA 137809.49 64 198 2153.27 2025-01-28 East USA 146303.02000000002 67 186 2183.63 2025-01-19 South India 371705.25999999983 156 471 2382.73 2025-01-27 East USA 196107.43000000008 78 237 2514.2 2025-01-12 APAC Japa

In [0]:
#analysis about monthly product performance
silver_sales = spark.table("main.default.silver_sales_s3")
product_master = spark.table("main.default.bronze_product_s3")

gold_monthly_product_performance = (
    silver_sales
    .join(
        product_master.select("product_id", "product_name", "category"),
        on="product_id",
        how="inner"
    )
    .withColumn("month", F.date_format("transaction_timestamp", "yyyy-MM"))
    .groupBy("month", "product_id", "product_name", "category")
    .agg(
        F.sum("total_amount").alias("revenue"),
        F.sum("quantity").alias("units_sold")
    )
    .withColumn(
        "avg_selling_price",
        F.round(F.col("revenue") / F.col("units_sold"), 2)
    )
)

gold_monthly_product_performance.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("main.default.gold_monthly_product_performance_s3")


In [0]:
display(spark.table("main.default.gold_monthly_product_performance_s3"))

month product_id product_name category revenue units_sold avg_selling_price 2025-01 PRD109 HP Pavilion Electronics 4947584.149999999 6287 786.95 2025-01 PRD108 Dell XPS 13 Electronics 4656984.38000001 6123 760.57 2025-01 PRD106 Levi's Jeans Apparel 5124241.0100000035 6542 783.28 2025-01 PRD104 Nike Air Max Sportswear 4889665.3599999985 6232 784.61 2025-01 PRD107 Sony Headphones Electronics 5039678.880000005 6492 776.29 2025-01 PRD105 Adidas Ultraboost Sportswear 4803211.660000002 6321 759.88 2025-01 PRD110 Apple Watch Wearables 5030212.2299999995 6589 763.43 2025-01 PRD103 AirPods Pro Accessories 4847516.060000007 6327 766.16 2025-01 PRD102 Galaxy S23 Electronics 5002204.8199999975 6568 761.6 2025-01 PRD101 iPhone 14 Electronics 5003427.279999996 6459 774.64

In [0]:
#revenue by regional sales summary
from pyspark.sql import functions as F

silver_sales = spark.table("main.default.silver_sales_s3")
gold_region_sales_summary = (
    silver_sales
    .groupBy("region", "country")
    .agg(
        F.sum("total_amount").alias("total_revenue"),
        F.countDistinct("transaction_id").alias("total_transactions"),
        F.sum("quantity").alias("total_units_sold")
    )
    .withColumn(
        "avg_transaction_value",
        F.round(
            F.col("total_revenue") / F.col("total_transactions"), 2
        )
    )
)

gold_region_sales_summary.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("main.default.gold_region_sales_summary_s3")

In [0]:
display(spark.table("main.default.gold_region_sales_summary_s3"))

region country total_revenue total_transactions total_units_sold avg_transaction_value West India 5013076.549999993 2159 6507 2321.94 South India 9918290.199999962 4337 13023 2286.9 APAC Australia 4720895.249999995 2039 6128 2315.3 APAC Japan 4835172.909999994 2088 6257 2315.7 East USA 5149536.399999999 2200 6687 2340.7 West USA 4877316.310000004 2121 6317 2299.54 Europe Germany 4870998.239999991 2091 6320 2329.51 APAC Singapore 4957390.429999991 2159 6455 2296.15 Europe UK 5002049.540000001 2082 6246 2402.52

In [0]:
%sql
--demonstrating time travel
DESCRIBE HISTORY main.default.silver_sales_s3;

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 2 2025-12-21T18:00:31.000Z 70588280163463 aspranavi1110@gmail.com CREATE OR REPLACE TABLE AS SELECT Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> true, properties -> {"delta.enableDeletionVectors":"true"}, statsOnLoad -> true) null List(4054221922185729) 1221-175710-7z9hfgf3-v2n 1 WriteSerializable false Map(numFiles -> 1, numRemovedFiles -> 1, numRemovedBytes -> 1140886, numDeletionVectorsRemoved -> 0, numOutputRows -> 21276, numOutputBytes -> 1140886) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13 1 2025-12-21T14:50:34.000Z 70588280163463 aspranavi1110@gmail.com CREATE OR REPLACE TABLE AS SELECT Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> true, properties -> {"delta.enableDeletionVectors":"true"}, statsOnLoad -> true) null List(2076262709341777) 1221-141552-yk1k5gcs-v2n 0 WriteSerializable false Map(numFiles -> 1, numRemovedFiles -> 1, numRemovedBytes -> 1140886, numDeletionVectorsRemoved -> 0, numOutputRows -> 21276, numOutputBytes -> 1140886) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13 0 2025-12-21T14:42:33.000Z 70588280163463 aspranavi1110@gmail.com CREATE OR REPLACE TABLE AS SELECT Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> true, properties -> {"delta.enableDeletionVectors":"true"}, statsOnLoad -> true) null List(2076262709341777) 1221-141552-yk1k5gcs-v2n null WriteSerializable false Map(numFiles -> 1, numRemovedFiles -> 0, numRemovedBytes -> 0, numDeletionVectorsRemoved -> 0, numOutputRows -> 21276, numOutputBytes -> 1140886) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13

In [0]:
%sql
--demonstrating version rollback
RESTORE TABLE main.default.silver_sales_s3
TO VERSION AS OF 2;

In [0]:
%sql
--verifying the rollback
SELECT COUNT(*) FROM main.default.silver_sales_s3;


COUNT(*) 21276

In [0]:
%sql
--optimizing table
OPTIMIZE main.default.silver_sales_s3;

path metrics List(0, 0, List(null, null, 0.0, 0, 0), List(null, null, 0.0, 0, 0), 0, null, null, 0, 0, 1, 1, true, 0, 0, 1766341273742, 1766341274592, 8, 0, null, List(0, 0), null, 11, 11, 0, 0, null)

In [0]:
#logging and error handling(error handling has already been implemented in the previous code)
from pyspark.sql import Row
from pyspark.sql import functions as F
from datetime import datetime

def log_pipeline_run(
    pipeline_name,
    layer,
    start_time,
    end_time,
    source_count,
    output_count,
    rejected_count,
    status,
    error_message=None
):
    log_row = [
        Row(
            pipeline_name=pipeline_name,
            layer=layer,
            start_time=start_time,
            end_time=end_time,
            source_count=source_count,
            output_count=output_count,
            rejected_count=rejected_count,
            status=status,
            error_message=error_message,
            run_timestamp=datetime.now()
        )
    ]

    spark.createDataFrame(log_row).write \
        .format("delta") \
        .mode("append") \
        .saveAsTable("main.default.pipeline_logs")
log_pipeline_run(
    pipeline_name="Retail_Analytics_Pipeline",
    layer="Silver",
    start_time=datetime.now(),
    end_time=datetime.now(),
    source_count=spark.table("main.default.bronze_sales_s3").count(),
    output_count=spark.table("main.default.silver_sales_s3").count(),
    rejected_count=spark.table("main.default.silver_sales_dq_quarantine_s3").count(),
    status="SUCCESS"
)



---------------------------------------------------------------------------
PySparkValueError                         Traceback (most recent call last)
File <command-6707673468359202>, line 36
     17     log_row = [
     18         Row(
     19             pipeline_name=pipeline_name,
   (...)
     29         )
     30     ]
     32     spark.createDataFrame(log_row).write \
     33         .format("delta") \
     34         .mode("append") \
     35         .saveAsTable("main.default.pipeline_logs")
---> 36 log_pipeline_run(
     37     pipeline_name="Retail_Analytics_Pipeline",
     38     layer="Silver",
     39     start_time=datetime.now(),
     40     end_time=datetime.now(),
     41     source_count=spark.table("main.default.bronze_sales_s3").count(),
     42     output_count=spark.table("main.default.silver_sales_s3").count(),
     43     rejected_count=spark.table("main.default.silver_sales_dq_quarantine_s3").count(),
     44     status="SUCCESS"
     45 )

File <command-6707

In [0]:
%sql
--we can now verify that the logs are now added into our pipeline_logs
SELECT * FROM main.default.pipeline_logs;


pipeline_name layer start_time end_time source_count output_count rejected_count status error_message run_timestamp Retail_Silver_Pipeline Silver 2025-12-21T18:31:16.449Z 2025-12-21T18:31:27.739Z 0 0 0 FAILED [CANNOT_DETERMINE_TYPE] Some of types cannot be determined after inferring. 2025-12-21T18:31:27.739Z